# Setup

In [1]:
# Uncomment if you want to automatically install all dependencies via pip
# !pip install -r requirements.txt

In [2]:
import matplotlib as mpl
import matplotlib.pyplot as plt

import numpy as np
import scipy

We use the [DER](https://arxiv.org/abs/1910.02600) implementation of Amini et al. from [PyPI](https://pypi.org/project/evidential-deep-learning/) and shamelessy [copy & paste one of their toy implementations](https://github.com/aamini/evidential-deep-learning/blob/main/hello_world.py).

In [3]:
import tensorflow as tf
import evidential_deep_learning as edl

Visualizations are generated in the `img/` directory using [nbfigtulz](https://pypi.org/project/nbfigtulz/).

In [4]:
!rm -rf img/understanding_sota && mkdir -p img/understanding_sota
import nbfigtulz as ftl

FIG_SIZE_SMALL = (3.0, 2.3)  # small images for paper
FIG_SIZE_LARGE = (4.0, 3.0)  # larger images for presentation
FIG_SIZE = FIG_SIZE_LARGE

For the sake of good reproducibility we fix the seed to a [random value](https://xkcd.com/221/) and try to reduce any dependency to this value later by sampling.

In [5]:
seed = 42
np.random.seed(seed)
tf.random.set_seed(seed)

In their example Amini et al. used the hyperparameter $\lambda = 0.01$, where $\lambda$ is the coupling constant in $\mathcal{L}_i = \mathcal{L}_i^\text{NLL} + \lambda \mathcal{L}_i^\text{R}$.

In [6]:
LAMBDA = .01

In order to exclude numerical implications due to reduced floating point precision one can switch TF's default value to `float64`. (We didn't find any major discrepancy.)

In [7]:
tf.keras.backend.set_floatx('float32')

# Overview

In [Multivariate Deep Evidential Regression](https://arxiv.org/abs/2104.06135) we found that *Deep Evidential Regression* (DER) as introduced by [Amini et al.](https://arxiv.org/abs/1910.02600)  has issues in its mathematical modelling. Our main objection is that the proposed loss function $\mathcal{L}_i = \mathcal{L}_i^\text{NLL} + \lambda \mathcal{L}_i^\text{R}$ with
$$\begin{align*}
    \mathcal{L}_i^\text{NLL} &= \frac{1}{2} \log \frac{\pi}{\nu} - \alpha \log \Omega + \left( \alpha + \frac{1}{2} \right) \log\!\left( (y_i -\gamma)^2 \nu + \Omega \right) + \log \Gamma(\alpha) - \log \Gamma\!\left( \alpha + \frac{1}{2}\right), \\
    \mathcal{L}_i^\text{R} &= |y_i - \gamma|(2\nu + \alpha),
\end{align*}$$
can easily be minimized by sending $\nu$ to zero if $\beta$ is adjusted according to:
$$\beta(\nu) = \beta_0 \frac{1 + \nu_0^{-1}}{1 + \nu^{-1}} \,,$$
where $\beta_0 > 0$ and $\nu_0 > 0$ are some arbitray initial values.
This is obvious by looking at the definition of the loss function using the Student's $t$-distribution, $\operatorname{St}_{2 \alpha}$ with $2\alpha$ degrees of freedom,
$$\mathcal{L}_i^\text{NLL} = \operatorname{St}_{2\alpha}\!\left( y_i \middle| \gamma, \frac{\beta (1 + \nu)}{\nu \alpha} \right),$$
due to the degeneration of its width since the product $\beta (1 + \nu) / \nu$ cannot be unfolded with $\mathcal{L}_i^\text{NLL}$.
A more formal proof can be found by showing that $\mathcal{L}_i^\text{NLL}$ does not depend on $\nu$ if one uses our above definition of $\beta(\nu)$.
We do so by calculating the derivative $\partial_\nu \mathcal{L}_i^\text{NLL}$,
$$\begin{align*}
\partial_\nu \left[ \frac{1}{2} \log\!\left( \frac{\pi}{\nu} \right) \right] &= -\frac{1}{2 \nu} \,, \\
\partial_\nu \left[ \alpha \log(\Omega) \right] &= -\frac{\alpha}{\nu} \,, \\
\partial_\nu \left[ \left( \alpha + \frac{1}{2} \right) \log\!\left( (y_i - \gamma)^2 \nu + \Omega \right) \right] &= \frac{\alpha + \frac{1}{2}}{\nu} \,,
\end{align*}$$
where we used the identities:
$$\begin{align*}
\partial_\nu \beta(\nu) &= \frac{\beta(\nu)}{\nu (1 + \nu)} \,, \\
\partial_\nu \Omega(\nu) &= \frac{\Omega(\nu)}{\nu} \,,
\end{align*}$$
to find the derviative of $\Omega = 2 \beta (1 + \nu)$.
The deriviate of $\mathcal{L}_i$ thus reads:
$$\partial_\nu \mathcal{L}_i = \partial_\nu \mathcal{L}_i^\text{NLL} + \lambda \, \partial_\nu \mathcal{L}_i^\text{R} = \underbrace{\frac{1}{\nu} \left( -\frac{1}{2} - \alpha + \alpha + \frac{1}{2} \right)}_{\partial_\nu \mathcal{L}_i^\text{NLL}} + \underbrace{2\lambda |y_i - \gamma|}_{\lambda \, \partial_\nu \mathcal{L}_i^\text{R}} = 2 \lambda |y_i - \gamma| \quad \forall \, \nu \,.$$
and shows that $\mathcal{L}_i^\text{NLL}$ is indeed independent of the parameter $\nu$ and the minimum of $\mathcal{L}_i^\text{R}$ at $\nu = 0$ also minimizes $\mathcal{L}_i$.

Despite this mathematical argument, there are a growing number of experiments that uses DER and actually find visually convincing results. In the following we will analyze DER in-depth in order to understand the reason for this, on first glance, unexpected outcome.

# Experiment

First, we generate training and testing data according to $f(x) = x^3$. For the testing data $x$ is taken from the interval $[-7, 7]$ and for the training data from $[-4, 4]$. Further, we add Gaussian noise with a standard deviation $\sigma = 3$ to the training data.

In [8]:
def generate_data(x_min, x_max, n, train=True):
    dtype = tf.keras.backend.floatx()
    
    x = np.linspace(x_min, x_max, n)
    x = np.expand_dims(x, -1).astype(dtype)

    sigma = 3. * np.ones_like(x) if train else np.zeros_like(x)
    y = x ** 3 + np.random.normal(0., sigma).astype(dtype)

    return x, y


x_train, y_train = generate_data(-4, 4, 1000)
x_test, y_test = generate_data(-7, 7, 1000, train=False)

We then define the loss function...

In [9]:
def loss(y, pred):
    return edl.losses.EvidentialRegression(y, pred, coeff=LAMBDA)

...and a helper function to train a shallow NN:

In [10]:
def fit(x, y, *, n_epochs=500, model=None):
    if model is None:
        model = tf.keras.Sequential([
            tf.keras.layers.Dense(64, activation="relu"),
            tf.keras.layers.Dense(64, activation="relu"),
            edl.layers.DenseNormalGamma(1),
        ])

        model.compile(optimizer=tf.keras.optimizers.Adam(5e-4), loss=loss)
        
    model.fit(x, y, batch_size=100, epochs=n_epochs, verbose=0)
    
    return model

Now, we train 25 independent models (500 epochs each) and save the predictions for $(\gamma, \nu, \alpha, \beta)$ where we evaluate the latter on the testing and trainings data, respectively. (This may take some time ☕)

In [11]:
preds_test = []
preds_train = []
for _ in range(25):
    model = fit(x_train, y_train)
    preds_test.append(model(x_test).numpy())
    preds_train.append(model(x_train).numpy())
    
preds_test = np.stack(preds_test)
preds_train = np.stack(preds_train)

preds_test.shape, preds_train.shape

((25, 1000, 4), (25, 1000, 4))

Let us now take a peek at the estimated epistemic uncertainty of the first 9 models...

In [12]:
@ftl.with_context
def make_fig(x_train, y_train, x_test, y_test, y_pred, *, n_stds=4, file_name):
    x_train = x_train[:, 0]
    y_train = y_train[:, 0]
    x_test = x_test[:, 0]
    y_test = y_test[:, 0]
    
    mu = pred[:, 0]
    v = pred[:, 1]
    alpha = pred[:, 2]
    beta = pred[:, 3]
    std = np.sqrt(beta / (v * (alpha - 1.)))
    
    fig, ax = plt.subplots()
        
    for i in np.arange(1, n_stds + 1):
        ax.fill_between(
            x_test,
            mu - i * std,
            mu + i * std,
            color='C0',
            alpha=.2,
            label='Epist.' if i == 1 else None
        )
        
    ax.scatter(x_train, y_train, s=5., c='black', label='Train.')
    ax.plot(x_test, y_test, '--', c='black', label='GT')
    ax.plot(x_test, mu, c='C1', label='Pred.')
    
    ax.set_xlabel('$x$')
    ax.set_ylabel('$y$')
    
    ax.legend()
    
    return ftl.save_fig(fig, file_name, resize=FIG_SIZE)


imgs = []
for i, pred in enumerate(preds_test[:9]):
    img = make_fig(x_train, y_train, x_test, y_test, pred, file_name=f'pred{i + 1}')
    imgs.append(img)
    

ftl.img_grid(imgs, n_columns=3, width=700)

This indeed looks convincing for most of the models -- although we notice that not all estimations find the same epistemic uncertainty for $x < -4$ and $x > +4$.

Let's generate some more visualization of the parameter estimations...

In [13]:
@ftl.with_context
def make_fig(x, vs, beta):
    fig, ax = plt.subplots()
    
    ax.set_xlabel('$x$')
    ax.set_yscale('log')
    ax.set_xlim(-7, 7)
    ax.grid()
    
    for i, (v, b) in enumerate(zip(vs, beta)):
        ax.plot(x, v, c='C0', alpha=.2)
        ax.plot(x, b, c='C1', alpha=.2)
        
    ax.legend([
        mpl.lines.Line2D([0], [0], c='C0'),
        mpl.lines.Line2D([0], [0], c='C1')
    ], [r'$\nu$', r'$\beta$'])
        
    return ftl.save_fig(fig, 'nu_beta', resize=FIG_SIZE)


make_fig(x_test[:, 0], preds_test[..., 1], preds_test[..., 3])

nu_beta.png

In [14]:
@ftl.with_context
def make_fig(x, vs):
    fig, ax = plt.subplots()
    
    ax.set_xlabel('$x$')
    ax.set_ylabel(r'$\sigma_\mathrm{St}$')
    ax.set_yscale('log')
    ax.set_xlim(-7, 7)
    ax.grid()
    
    for v in vs:
        ax.plot(x, v, c='C0', alpha=.2)
        
    return ftl.save_fig(fig, 'width', resize=FIG_SIZE)


v = preds_test[..., 1]
a = preds_test[..., 2]
b = preds_test[..., 3]
w = make_fig(x_test[:, 0], np.sqrt(b * (1. + v) / v / a))

In [15]:
@ftl.with_context
def make_fig(x, alphas):
    fig, ax = plt.subplots()
     
    ax.set_xlabel('$x$')
    ax.set_ylabel(r'$\alpha$')
    ax.set_xlim(-7, 7)
    ax.grid()
    
    for a in alphas:
        ax.plot(x, a, c='C0', alpha=.2)
        
    return ftl.save_fig(fig, 'alpha', resize=FIG_SIZE)


alpha = make_fig(x_test[:, 0], preds_test[..., 2])

In [16]:
ftl.img_grid([w, alpha])

""


We see that the order of magnitude for $\nu$ is very low, even in regions with low epistemic uncerainty. Since $\nu$ and $\alpha$ can be interpreted as the number of virtual measurements corresponding to the prior information one would naively expect that these numbers are much closer and larger (if not much larger) than one.

In [17]:
@ftl.with_context
def make_fig(x, uncs, label, *, file_name):
    fig, ax = plt.subplots()
    
    for unc in uncs:
        ax.plot(x, unc, c='C0', alpha=.2)

    ax.set_xlabel('$x$')
    ax.set_xlim(-7, 7)
    ax.grid()
    ax.legend([
        mpl.lines.Line2D([0], [0], c='C0'),
    ], [label,])
        
    return ftl.save_fig(fig, file_name, resize=FIG_SIZE)


v = preds_test[..., 1]
a = preds_test[..., 2]
b = preds_test[..., 3]
unc1 = make_fig(x_test[:, 0], np.sqrt(b / (a - 1)), 'Aleatoric', file_name='aleatoric')
unc2 = make_fig(x_test[:, 0], np.sqrt(b / (a - 1) / v), 'Epistemic', file_name='epistemic')
ftl.img_grid([unc1, unc2])

,


Similarly, the estimation of the aleatoric uncertainty peaks at $x \approx 0$ with a peak height of $\sigma \approx 1$ which conflicts with the expected uniform distribution with a height of $\sigma = 3$ (at least for $-4 < x < 4$).

Next, we take a look at the prediction error $y_i - \gamma$...

In [18]:
@ftl.with_context
def make_fig(x, dys):
    fig, ax = plt.subplots()
    
    ax.set_xlabel('$x$')
    ax.set_ylabel(r'$|y_i - \gamma|$')
    ax.set_xlim(-7, 7)
    ax.set_yscale('log')
    ax.grid()
    
    for dy in dys:
        ax.plot(x, dy, c='C0', alpha=.1)
        
    return ftl.save_fig(fig, 'dy', resize=FIG_SIZE)


dy = make_fig(x_test[:, 0], np.abs(preds_test[..., 0] - y_test[:, 0]))

In [19]:
@ftl.with_context
def make_fig(x, dys):
    fig, ax = plt.subplots()
    
    ax.set_xlabel('$x$')
    ax.set_ylabel(r'$(y_i - \gamma)^2$')
    ax.set_xlim(-4, 4)
    ax.set_ylim(0, 2.5)
    ax.grid()
    
    for dy in dys:
        ax.plot(x, dy, c='C0', alpha=.1)
        
    return ftl.save_fig(fig, 'dy2', resize=FIG_SIZE)


dy2 = make_fig(x_test[:, 0], (preds_test[..., 0] - y_test[:, 0]) ** 2)

In [20]:
ftl.img_grid([dy, dy2])

... as well as the components of the loss $\mathcal{L}_i$:

In [21]:
@ftl.with_context
def make_fig(x, dys):
    fig, ax = plt.subplots()
    
    ax.set_xlabel('$x$')
    ax.set_ylabel(r'$\lambda \mathcal{L}_i^\mathrm{R}$')
    ax.set_xlim(-4, 4)
    ax.set_ylim(0, .05)
    ax.grid()
    
    for dy in dys:
        ax.plot(x, dy * LAMBDA, c='C0', alpha=.1)
        
    return ftl.save_fig(fig, 'lr', resize=FIG_SIZE)


g = preds_test[..., 0]
v = preds_test[..., 1]
a = preds_test[..., 2]
make_fig(x_test[:, 0], np.abs(y_test[:, 0] - g) * (2. * v + a))

lr.png

In [22]:
def nll(y, p):
    g = p[:, 0]
    v = p[:, 1]
    a = p[:, 2]
    b = p[:, 3]
    omega = 2. * b * (1. + v)
    
    return np.stack([
        .5 * np.log(np.pi / v),
        -a * np.log(omega),
        (a + .5) * np.log((y[:, 0] - g)**2 * v + omega),
        scipy.special.loggamma(a) - scipy.special.loggamma(a + .5)
    ]).T


n = 200
l1 = edl.losses.EvidentialRegression(y_train[0:n], preds_train[0][0:n], coeff=0.).numpy()
l2 = np.sum(nll(y_train[0:n], preds_train[0][0:n])) / n
assert np.isclose(l1, l2)

In [23]:
@ftl.with_context
def make_fig(x, y, ps, *, file_name):
    fig, ax = plt.subplots()
    
    for p in ps:
        cs = nll(y, p)
        ax.plot(x[:, 0], np.sum(cs, axis=1), c='black', alpha=.1, zorder=1)
        ax.plot(x[:, 0], cs[:, 0], c='C0', alpha=.2, zorder=2)
        ax.plot(x[:, 0], cs[:, 1], c='C1', alpha=.2, zorder=3)
        ax.plot(x[:, 0], cs[:, 2], c='C2', alpha=.2, zorder=4)
        ax.plot(x[:, 0], cs[:, 3], c='C3', alpha=.2, zorder=5)
        
    ax.legend([
        mpl.lines.Line2D([0], [0], c='black'),
        mpl.lines.Line2D([0], [0], c='C0'),
        mpl.lines.Line2D([0], [0], c='C1'),
        mpl.lines.Line2D([0], [0], c='C2'),
        mpl.lines.Line2D([0], [0], c='C3'),
    ], ['Sum', r'\#1', r'\#2', r'\#3', r'\#4'])
    
    ax.set_xlim(-4, 4)
    ax.set_ylim(-15, 15)
    ax.set_xlabel('$x$')
    ax.grid()
    
    return ftl.save_fig(fig, file_name, resize=FIG_SIZE)
        
nll_test = make_fig(x_test, y_test, preds_test, file_name='nll_test')
nll_train = make_fig(x_train, y_train, preds_train, file_name='nll_train')
ftl.img_grid([nll_test, nll_train])

,


where we used the abbreviations $\#i$ to refer to the components of $\mathcal{L}_i^\text{NLL}$,
$$\mathcal{L}_i^\text{NLL} =
\underbrace{\frac{1}{2} \log \frac{\pi}{\nu}}_{\#1}
- \underbrace{\alpha \log \Omega}_{\#2}
+ \underbrace{\left( \alpha + \frac{1}{2} \right) \log\!\left( (y_i -\gamma)^2 \nu + \Omega \right)}_{\#3}
+ \underbrace{\log \Gamma(\alpha) - \log \Gamma\!\left( \alpha + \frac{1}{2}\right)}_{\#4} \,.
$$

# Understanding DER

The reason why the minimization of $\mathcal{L}_i$ does not converge to the optimal minimum with $\nu = 0$ is the large difference in the order of magnitudes of $\mathcal{L}_i^\text{NLL}$ and $\lambda \mathcal{L}_i^\text{R}$ (which resembles the [problem in multi-task learning](https://arxiv.org/abs/2001.06782)). Below we show an example where we reduce $\nu$ by 50% (and adjust $\beta$ accordingly) which causes only a tiny reduction of roughly 0.02% in $\mathcal{L}_i$:

In [24]:
v = preds_train[:, :, 1]
b = preds_train[:, :, 3]
w = b * (1. + v) / v

v2 = .5 * v
b2 = b * (v2 / v + v2) / (1. + v2)
w2 = b2 * (1. + v2) / v2

preds2 = np.copy(preds_train)
preds2[:, :, 1] = v2
preds2[:, :, 3] = b2

assert np.allclose(w, w2)

l1 = loss(y_train, preds_train[0]).numpy()
l2 = loss(y_train, preds2[0]).numpy()

print(f'L1: {l1:g}, L2: {l2:g} ({(l1 / l2 - 1) * 100:g}%)')
assert l1 > l2

L1: 2.55559, L2: 2.55508 (0.0199556%)


Optimizers tend to stop if the improvement falls below a certain threshold, i.e., $\mathcal{L}_i^\text{NLL}$ is typically larger than $\mathcal{L}_i^\text{R}$ but only the latter yields a non-zero gradient for $\nu$. Hence, the gradient of $\nu$ dies out if $\partial_\nu \mathcal{L}_i^\text{R} = 2 |y_i - \gamma|$ becomes small. It is therefore the initial deviation between prediction and observed data as well as the convergence speed that decides when decreasing $\nu$ does not contribute to a sufficiently improvement of the loss function. In our example this is the case for regions at the boundaries $x \approx \pm 4$ but not at the center $x \approx 0$ as we can see by plotting the prediction error, $y_i - \gamma$, after training the model for different numbers of epochs.

In [25]:
model = None
preds = []
for _ in range(4):
    model = fit(x_train, y_train, n_epochs=50, model=model)
    preds.append(model(x_train).numpy())
    
preds = np.stack(preds)

In [26]:
@ftl.with_context
def make_fig(x, dys):
    fig, ax = plt.subplots()
    
    ls = ['solid', 'dotted', 'dashed', 'dashdot']
    for i, dy in enumerate(dys):
        ax.plot(x, dy, c=f'C{i}', linestyle=ls[i], label=f'{(i + 1) * 50}')
    
    ax.set_xlabel('$x$')
    ax.set_ylabel(r'$\gamma - x^3$')
    ax.grid()
    ax.legend()
        
    return ftl.save_fig(fig, 'dys', resize=FIG_SIZE)


make_fig(x_train[:, 0], preds[..., 0] - x_train[:, 0] ** 3)

dys.png

We see the same behavior in the ratio of $\mathcal{L}_i^\text{R}$ and $\mathcal{L}_i^\text{NLL}$ where we find large values at the boundaries, corresponding to large gradients of $\nu$, which decay during training.

In [27]:
@ftl.with_context
def make_fig(x, y, preds):
    fig, ax = plt.subplots()
    
    ls = ['dashed', 'solid', 'dashed']
    for i, idx in enumerate([0, x.shape[0] // 2, x.shape[0] - 1]):
        l1 = np.array([np.sum(nll(y, p), axis=1)[idx] for p in preds])
        l2 = np.array([LAMBDA * np.abs(y[idx, 0] - p[idx, 0]) * (2. * p[idx, 1] + p[idx, 2]) for p in preds])
        ax.plot(l2 / l1, 'o', linestyle=ls[i], label=f'$x={x[idx, 0]:+.0f}$')
    
    ax.set_xticks([0, 1, 2, 3])
    ax.set_xticklabels(['50', '100', '150', '200'])
    ax.set_xlabel('Epochs')
    ax.set_ylabel(r'$\lambda \mathcal{L}_i^\mathrm{R} / \mathcal{L}_i^\mathrm{NLL}$')
    ax.legend()
    
    return ftl.save_fig(fig, 'lr_lnll', resize=FIG_SIZE)
    

make_fig(x_train, y_train, preds)

lr_lnll.png